In [1]:
import os
import pandas as pd
import numpy as np
from src.utils.project_paths import DATA_PATH
# pd.set_option('display.max_rows', 100)

In [2]:
df = pd.read_csv(os.path.join(DATA_PATH, 'ILVCoreStakesPerAddress.csv'))
staked_events = pd.read_csv(os.path.join(DATA_PATH, 'staked_events.csv'))
unstaked_events = pd.read_csv(os.path.join(DATA_PATH, 'unstaked_events.csv'))
transfer_events = pd.read_csv(os.path.join(DATA_PATH, 'transfer_events.csv'))

In [6]:
staked_events.amount = staked_events.amount.astype(np.float_)
unstaked_events.amount = unstaked_events.amount.astype(np.float_)
transfer_events.value = transfer_events.value.astype(np.float_)

In [8]:
staked_events.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 31577 entries, 0 to 31576
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   address      31577 non-null  object 
 1   blockNumber  31577 non-null  int64  
 2   amount       31577 non-null  float64
 3   Pool         31577 non-null  object 
dtypes: float64(1), int64(1), object(2)
memory usage: 986.9+ KB


In [7]:
balances = staked_events[staked_events.Pool == "ILV-ETH LP"].groupby("address")[["amount"]].sum().merge(
    unstaked_events[unstaked_events.Pool == "ILV-ETH LP"].groupby("address")[["amount"]].sum(),
    how="outer", left_index=True, right_index=True).fillna(0).rename(
    columns={"amount_x": "Staked", "amount_y": "Unstaked"})

In [10]:
balances['total_amount'] = balances['Staked'] - balances['Unstaked']

In [11]:
balances.sort_values('total_amount', ascending=False)

Staked      Unstaked  \
address                                                                  
0x2079C29Be9c8095042edB95f293B5b510203d6cE  1.611339e+22  5.354691e+21   
0xA1175a219dac539F2291377F77afD786D20e5882  6.956461e+21  1.872453e+21   
0xC33ED9cEd28850add236d475812b21BACFBB8812  1.781142e+22  1.455008e+22   
0xb5BE97C440D573e81Ea3d2257432EB2aE646e265  1.582201e+22  1.323317e+22   
0x22a197b1029523e2b4213ADFe762193182eC9757  9.563944e+21  7.228937e+21   
...                                                  ...           ...   
0xAc143174CDab4364d8B05019D25D9519D27461eD  2.975727e+18  2.975727e+18   
0x42309aB9681352613bfFfb6Df39AcD25E7444Ef6  3.714332e+18  3.714332e+18   
0xbbfbCe1b54435F97853433B1A3f46cf5375d1947  5.876248e+18  5.876248e+18   
0xBf6950E96719AAcD1F787bE2E6c99359a2500402  1.031165e+19  1.031165e+19   
0xF7A819DEBA0d69C4f3567cb9fAc04B05Ec3A6516  7.774506e+19  7.774506e+19   

                                            total_amount  
address                                                   
0x2079C29Be9c8095042edB95f293B5b510203d6cE  1.075869e+22  
0xA1175a219dac539F2291377F77afD786D20e5882  5.084008e+21  
0xC33ED9cEd28850add236d475812b21BACFBB8812  3.261343e+21  
0xb5BE97C440D573e81Ea3d2257432EB2aE646e265  2.588834e+21  
0x22a197b1029523e2b4213ADFe762193182eC9757  2.335007e+21  
...                                                  ...  
0xAc143174CDab4364d8B05019D25D9519D27461eD -5.120000e+02  
0x42309aB9681352613bfFfb6Df39AcD25E7444Ef6 -5.120000e+02  
0xbbfbCe1b54435F97853433B1A3f46cf5375d1947 -1.024000e+03  
0xBf6950E96719AAcD1F787bE2E6c99359a2500402 -2.048000e+03  
0xF7A819DEBA0d69C4f3567cb9fAc04B05Ec3A6516 -1.638400e+04  

[8444 rows x 3 columns]

In [12]:
df.head()

address                Staked  \
0  0x00000003243ffabd3a3895cf83192AEe1B2cDE31  19000000000000000000   
1  0x000082301dAAd1D389F54d71e660097ecC79eb89  12084618800000000000   
2  0x0002208085F5e1946500aD6616aA0Ee2f19e826d   3981270138246641223   
3  0x000334dCDdA7E848B206CCA09BaF033823C72846   2046044258806547424   
4  0x000433708645EaaD9f65687CDbe4033d92f6A6d2   8871017043504012117   

              Unstaked  
0                    0  
1                    0  
2                    0  
3                    0  
4  8871017043504012117

In [14]:
df['total_amount'] = df['Staked'].astype(np.float_) - df['Unstaked'].astype(np.float_)

In [16]:
df.sort_values('total_amount', ascending=False)

address                   Staked  \
5773   0x6e3AA85dB95BBA36276a37ED93B12B7AB0782aFB  41425401613302507776984   
5353   0x667e89535f11505A85DD5429Ece483F268685971  12194877017608926656145   
552    0x0Aa3BE46401579beCfDab425Afce84Ae5DA851dC   4586336335475837054692   
8053   0x9Bb3D4cC7251FA56440E0145162319FCFECCF975   7953165395727319144516   
12620  0xe4Bc96b24e0bDF87b4b92Ed39C1AEf8839b090dd   9995621757981372091974   
...                                           ...                      ...   
10372  0xED7a86ebDd39bC4A9339D0Aa3bb91B497cAF7686     20000000000000000000   
10373  0xED878738872C0a63CB0ab32Ed1AFd874A1e84410      1000000000000000000   
2489   0x2eB88e6c56dC9889c338f31BCF93B316f9D498F8      1886629745868783248   
2487   0x2e7FF9Dd3E4e9822798e5847DE0593a7b0b1042A    200035189388803637416   
2184   0x2A0626380Bf336cd9493BfeD74966d53B6b9101E     17169215796863639439   

                      Unstaked  total_amount  
5773   34425401613302507776984  7.000000e+21  
5353    6194877017608926656145  6.000000e+21  
552                          0  4.586336e+21  
8053    4953165395727319144516  3.000000e+21  
12620   7663257497981372091974  2.332364e+21  
...                        ...           ...  
10372     20000000000000000000  0.000000e+00  
10373      1000000000000000000  0.000000e+00  
2489       1886629745868783248  0.000000e+00  
2487     200035189388803637416  0.000000e+00  
2184      17169215796863639439  0.000000e+00  

[13329 rows x 4 columns]

In [14]:
from src.gini_lorenz.lorenz_visualization import LorenzCurve
lorenz_curve = LorenzCurve(list(x.loc[(x['amount'] > 0) & (x['month'] == 12)].sort_values('amount', ascending=True).amount))
lorenz_curve.plot_lorenz()

In [15]:
lorenz_curve.plot_lorenz_by_month(df=x)

0.6
0.73
0.52
0.79
0.89
0.75
0.95
0.93
0.96
1.0


In [ ]:
import os
from src.utils.project_paths import DATA_RAW, DATA_PROCESSED

transfer_events = pd.read_csv(os.path.join(DATA_RAW, 'transfer_events.csv'))
transfer_events.value = transfer_events.value.astype(np.float_)

In [ ]:
from_value = transfer_events[['from', 'value']]
to_value = transfer_events[['to', 'value']]

In [ ]:
from_value_x = from_value.groupby('from').value.sum().reset_index()

In [ ]:
to_value_x = to_value.groupby('to').value.sum().reset_index()

In [ ]:
from_value_x['value'] = from_value_x.apply(lambda x: x['value'] * (-1), axis=1)

In [ ]:
from_value_x.columns = ['address', 'value']
to_value_x.columns = ['address', 'value']

In [ ]:
balances = from_value_x.merge(to_value_x, how="outer", on=['address']).fillna(0).rename(columns={"value_x": "value_from", "value_y": "value_to"})

In [ ]:
balances['amount'] = balances['value_from'] + balances['value_to']

In [ ]:
# balances[['address', 'amount']].to_csv(os.path.join(DATA_PROCESSED, 'ilv.csv'), index=False)